# Preparation of the Jupyter notebook kernel

conda create --name llama python=3.10
   conda activate llama 
    pip install git+https://github.com/huggingface/transformers.git
    pip install git+https://github.com/huggingface/peft.git
  925  pip install git+https://github.com/huggingface/accelerate.git 
  926  pip install -q -U trl
  927  pip install -q trl
  928  pip install -U datasets
  929  pip install -U bitsandbytes 
  930  pip install -U einops
  931  pip install -U wandb
  932  pip install --user ipykernal
  933  pip install --user ipykernel
  934  python -m ipykernel install --user --name=llama

So now you can open jupyter notebook and select the "llama" kernel to run the notebook

In [2]:
# The following command checks how many GPUs are availble in the current system to use
!nvidia-smi

Tue Nov 21 20:16:12 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100 80G...  On   | 00000000:65:00.0 Off |                    0 |
| N/A   57C    P0   109W / 300W |  14197MiB / 81920MiB |     24%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
|   1  NVIDIA A100 80G...  On   | 00000000:CA:00.0 Off |                    0 |
| N/A   

## Preprocessing

The purpose of this step is to take the original file downloaded from HPO website, and make a simple JSON file that can be used by LLAMA fine-tuning later on.

In [3]:
import json

### Below is code to load in OMIM and ORPHA data

In [4]:
file_path = '/mnt/isilon/wang_lab/wanga18/projects/llama2/phenotype.hpoa'

# Create dictionaries to store disease data
disease_data = {}  # Key: Disease Name, Value: Tuple(Disease IDs, OMIM IDs)

# Read and extract data from the file
with open(file_path, 'r') as file:
    for line in file:
        columns = line.strip().split('\t')
        if len(columns) >= 4:
            disease_name = columns[1]
            omim_id = columns[0]


            if disease_name not in disease_data:
                disease_data[disease_name] = omim_id
                
        

In [5]:
from itertools import islice

for key, value in islice(disease_data.items(), 10):
    print(f"Key: {key}, Value: {value}")

Key: disease_name, Value: database_id
Key: Developmental and epileptic encephalopathy 96, Value: OMIM:619340
Key: Pseudohyperkalemia, familial, 2, due to red cell leak, Value: OMIM:609153
Key: Immunoglobulin kappa light chain deficiency, Value: OMIM:614102
Key: White-Kernohan syndrome, Value: OMIM:619426
Key: Diarrhea 4, malabsorptive, congenital, Value: OMIM:610370
Key: Short QT syndrome 2, Value: OMIM:609621
Key: Premature centromere division, Value: OMIM:212790
Key: Inflammatory bowel disease 25, early onset, autosomal recessive, Value: OMIM:612567
Key: Congenital prothrombin deficiency, Value: OMIM:613679


In [6]:
omim_orpha_data = []
test_data = []

for disease_name in disease_data:
    
    disease_id = disease_data[disease_name] #extract disease and its HPO ID from existing array 
    
    if ',' in disease_name:
        substrings = disease_name.split(', ') #split by comma 
        reversed_substrings = substrings[::-1] # reverse the list of substrings    
        disease_name = ' '.join(reversed_substrings) #join back reversed substrings 

    ORPHA = 'ORPHA:'
    OMIM = 'OMIM:'
    
    if OMIM in disease_id: #seperate by OMIM and ORPHA ID 
        omim_orpha_data.append({'input':f"""The Online Mendelian Inheritance in Man term {disease_name} is identified by the OMIM ID""", 'output':disease_id})
        omim_orpha_data.append({'input':f"""The OMIM ID of {disease_name} corresponds to""", 'output':disease_id})
        omim_orpha_data.append({'input':f"""The OMIM term {disease_name} has an OMIM ID of""", 'output':disease_id})
        test_data.append({'input':f"""OMIM ID of {disease_name} is""", 'output':disease_id})
        test_data.append({'input':f"""OMIM {disease_name} is""", 'output':disease_id})

    
    else:
        omim_orpha_data.append({'input':f"""The Orphanet term {disease_name} is identified by the Orphanet ID""", 'output':disease_id})
        omim_orpha_data.append({'input':f"""The Orphanet ID of {disease_name} corresponds to""", 'output':disease_id})
        omim_orpha_data.append({'input':f"""The Orphanet term {disease_name} has an Orphanet ID of""", 'output':disease_id})
        test_data.append({'input':f"""Orphanet ID of {disease_name} is""", 'output':disease_id})
        test_data.append({'input':f"""Orphanet {disease_name} is""", 'output':disease_id})


In [7]:
print(len(omim_orpha_data))
print(len(test_data))

36219
24146


In [8]:
omim_orpha_subset = omim_orpha_data

In [9]:
#dump the newly generated data subset into a JSON file 
with open("omim_train_part1.json", "w") as f: 
   json.dump(omim_orpha_subset, f)
with open("omim_train_part2.json", "w") as f: 
   json.dump(test_data, f)

## Setup

In [10]:
import pandas as pd
import transformers
import textwrap
from transformers import LlamaTokenizer, LlamaForCausalLM
import os
import sys
from typing import List

from peft import (
    LoraConfig,
    get_peft_model,
    get_peft_model_state_dict,
    prepare_model_for_int8_training,
)

import torch
from datasets import load_dataset
import pandas as pd

import json

DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
DEVICE

/home/wanga18/miniconda3/envs/llama/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


'cuda'

## Model load & data load

In [11]:
#extract the data from the JSON file 
train_data = load_dataset("json", data_files="omim_train_part1.json")
test_data = load_dataset("json", data_files="omim_train_part2.json")

Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 210.86it/s]
Generating train split: 36219 examples [00:00, 155613.68 examples/s]
Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 217.21it/s]
Generating train split: 24146 examples [00:00, 543158.29 examples/s]


In [12]:
len(train_data)


1

In [13]:
train_list = train_data['train']
test_list = test_data['train']

train_list

Dataset({
    features: ['input', 'output'],
    num_rows: 36219
})

In [ ]:
print(train_list['output'])

['database_id', 'database_id', 'database_id', 'OMIM:619340', 'OMIM:619340', 'OMIM:619340', 'OMIM:609153', 'OMIM:609153', 'OMIM:609153', 'OMIM:614102', 'OMIM:614102', 'OMIM:614102', 'OMIM:619426', 'OMIM:619426', 'OMIM:619426', 'OMIM:610370', 'OMIM:610370', 'OMIM:610370', 'OMIM:609621', 'OMIM:609621', 'OMIM:609621', 'OMIM:212790', 'OMIM:212790', 'OMIM:212790', 'OMIM:612567', 'OMIM:612567', 'OMIM:612567', 'OMIM:613679', 'OMIM:613679', 'OMIM:613679', 'OMIM:614116', 'OMIM:614116', 'OMIM:614116', 'OMIM:612201', 'OMIM:612201', 'OMIM:612201', 'OMIM:137580', 'OMIM:137580', 'OMIM:137580', 'OMIM:619354', 'OMIM:619354', 'OMIM:619354', 'OMIM:117650', 'OMIM:117650', 'OMIM:117650', 'OMIM:616067', 'OMIM:616067', 'OMIM:616067', 'OMIM:108770', 'OMIM:108770', 'OMIM:108770', 'OMIM:112700', 'OMIM:112700', 'OMIM:112700', 'OMIM:612229', 'OMIM:612229', 'OMIM:612229', 'OMIM:614880', 'OMIM:614880', 'OMIM:614880', 'OMIM:615546', 'OMIM:615546', 'OMIM:615546', 'OMIM:116200', 'OMIM:116200', 'OMIM:116200', 'OMIM:607

In [15]:
CUTOFF_LEN = 512

## Inference

In [16]:
BASE_MODEL = "/mnt/isilon/wang_lab/jingye/projects/llama2/hf/7B"
lora_weights = '/mnt/isilon/wang_lab/wanga18/projects/llama2/training_code/experiments_llama2/official_runs/OMIM_ORPHA_MODEL/50epochs_SBATCH'

In [17]:
load_8bit = False

In [18]:
model = LlamaForCausalLM.from_pretrained(
            BASE_MODEL,
            load_in_8bit=load_8bit,
             torch_dtype=torch.float16,
            device_map = "auto"
        )

Loading checkpoint shards: 100%|██████████| 2/2 [00:05<00:00,  2.73s/it]


In [19]:

from peft import PeftModel
model = PeftModel.from_pretrained(
            model,
            lora_weights,
            torch_dtype=torch.float16,
        )


In [21]:
tokenizer = LlamaTokenizer.from_pretrained(BASE_MODEL)

You are using the default legacy behaviour of the <class 'transformers.models.llama.tokenization_llama.LlamaTokenizer'>. This means that tokens that come after special tokens will not be properly handled. We recommend you to read the related pull request available at https://github.com/huggingface/transformers/pull/24565, and set the legacy attribute accordingly.


In [22]:
model.config.pad_token_id = tokenizer.pad_token_id = 0  # unk
model.config.bos_token_id = 1
model.config.eos_token_id = 2

In [23]:
from transformers import GenerationConfig
generation_config = GenerationConfig(
            temperature=0.1,
            top_p=0.5,
        )

/home/wanga18/miniconda3/envs/llama/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:362: UserWarning: `do_sample` is set to `False`. However, temperature is set to 0.1 -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset temperature. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/home/wanga18/miniconda3/envs/llama/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:367: UserWarning: `do_sample` is set to `False`. However, top_p is set to 0.5 -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset top_p. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(


In [24]:
prompt = f"""The Online Mendelian Inheritance in Man term Rubinstein-Taybi syndrome 2 is identified by the OMIM ID OMIM:"""

prompt = f"""The human phenotype ontology term (HPO) ID for """

In [76]:
inputs = tokenizer(prompt, return_tensors="pt")

In [77]:
input_ids = inputs["input_ids"].to('cuda')

In [79]:
with torch.no_grad():
    generation_output = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
        max_new_tokens=60,
    )

In [ ]:
generation_output

In [81]:
s = generation_output.sequences[0]
output = tokenizer.decode(s)
print(output)

<s> The Online Mendelian Inheritance in Man term Rubinstein-Taybi syndrome 2 is identified by the OMIM ID OMIM: 158100.
The Online Mendelian Inheritance in Man term Rubinstein-Taybi syndrome 2 is also known as RTS2.</s>


In [ ]:
#code below is combined steps above but all in a for loop 

predictionsCorrect = 0 #correct predictions 
predictionsIncorrect = 0 #incorrect predictions 

for i in range(0, len(train_list)-1): #loop through all fine-tuned diseases
    disease_name = train_list['input'][i] #get disease name 
    disease_id = train_list['output'][i] #get corresponding disease ID (HPO)
    
    if 'OMIM' in disease_id:
        prompt = f"""{disease_name} OMIM:"""
    else:
        prompt = f"""{disease_name} ORPHA:"""
        

    inputs = tokenizer(prompt, return_tensors="pt")
    input_ids = inputs["input_ids"].to('cuda')

    
    with torch.no_grad():
        generation_output = model.generate(
            input_ids=input_ids,
            generation_config=generation_config,
            return_dict_in_generate=True,
            output_scores=True,
            max_new_tokens=60,
        )
        
    generation_output #generate answer 
    s = generation_output.sequences[0]
    output = tokenizer.decode(s) #decode into string 
    
    print("--------------------------") #seperator line for clarity 
    
    if disease_id in output: #check if the output contains the correct HPO ID 
        #print(f"TRUE\n{disease_name} {output}\nANSWER: {hpo_id}\n")
        predictionsCorrect +=1 
    else:
        print(f"FALSE\n{disease_name}{output}\nANSWER: {disease_id}\n")
        predictionsIncorrect +=1
        print(f"INCORRECT: {totalIncorrect}, CORRECT: {totalCorrect}")

--------------------------
FALSE
The Orphanet term disease_name is identified by the Orphanet ID<s> The Orphanet term disease_name is identified by the Orphanet ID ORPHA:411677</s>
ANSWER: database_id

INCORRECT: 1, CORRECT: 0
--------------------------
FALSE
The Orphanet ID of disease_name corresponds to<s> The Orphanet ID of disease_name corresponds to ORPHA:67037</s>
ANSWER: database_id

INCORRECT: 2, CORRECT: 0
--------------------------
FALSE
The Orphanet term disease_name has an Orphanet ID of<s> The Orphanet term disease_name has an Orphanet ID of ORPHA:488677</s>
ANSWER: database_id

INCORRECT: 3, CORRECT: 0
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
-------------------------

--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
-

In [ ]:
print(f"finished validating on trained sentences")
print(f"total correct: {predictionsCorrect}")
print(f"total incorrect: {predictionsIncorrect}")

In [25]:
#code below is combined steps above but all in a for loop 

totalCorrect = 0 #correct predictions 
totalIncorrect = 0 #incorrect predictions 

for i in range(0, len(test_list)-1): #loop through all fine-tuned diseases
    disease_name = test_list['input'][i] #get disease name 
    disease_id = test_list['output'][i] #get corresponding disease ID (HPO)
    
    if 'OMIM' in disease_id:
        prompt = f"""{disease_name} OMIM:"""
    else:
        prompt = f"""{disease_name} ORPHA:"""
        

    inputs = tokenizer(prompt, return_tensors="pt")
    input_ids = inputs["input_ids"].to('cuda')

    
    with torch.no_grad():
        generation_output = model.generate(
            input_ids=input_ids,
            generation_config=generation_config,
            return_dict_in_generate=True,
            output_scores=True,
            max_new_tokens=60,
        )
        
    generation_output #generate answer 
    s = generation_output.sequences[0]
    output = tokenizer.decode(s) #decode into string 
    
    print("--------------------------") #seperator line for clarity 
    
    if disease_id in output: #check if the output contains the correct HPO ID 
        #print(f"TRUE\n{disease_name} {output}\nANSWER: {hpo_id}\n")
        totalCorrect +=1 
    else:
        print(f"FALSE\n{disease_name}{output}\nANSWER: {disease_id}\n")
        totalIncorrect +=1
        print(f"INCORRECT: {totalIncorrect}, CORRECT: {totalCorrect}")

/home/wanga18/miniconda3/envs/llama/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:362: UserWarning: `do_sample` is set to `False`. However, temperature is set to 0.1 -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset temperature.
  warnings.warn(
/home/wanga18/miniconda3/envs/llama/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:367: UserWarning: `do_sample` is set to `False`. However, top_p is set to 0.5 -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset top_p.
  warnings.warn(


--------------------------
FALSE
Orphanet ID of disease_name is<s> Orphanet ID of disease_name is ORPHA:271466</s>
ANSWER: database_id

INCORRECT: 1, CORRECT: 0
--------------------------
FALSE
Orphanet disease_name is<s> Orphanet disease_name is ORPHA:277197</s>
ANSWER: database_id

INCORRECT: 2, CORRECT: 0
--------------------------
--------------------------
--------------------------
--------------------------
FALSE
OMIM due to red cell leak 2 familial Pseudohyperkalemia is<s> OMIM due to red cell leak 2 familial Pseudohyperkalemia is OMIM:609865</s>
ANSWER: OMIM:609153

INCORRECT: 3, CORRECT: 3
--------------------------
FALSE
OMIM ID of Immunoglobulin kappa light chain deficiency is<s> OMIM ID of Immunoglobulin kappa light chain deficiency is OMIM:614004</s>
ANSWER: OMIM:614102

INCORRECT: 4, CORRECT: 3
--------------------------
FALSE
OMIM Immunoglobulin kappa light chain deficiency is<s> OMIM Immunoglobulin kappa light chain deficiency is OMIM:242100</s>
ANSWER: OMIM:614102

IN

--------------------------
--------------------------
--------------------------
--------------------------
FALSE
OMIM type 7 Episodic ataxia is<s> OMIM type 7 Episodic ataxia is OMIM:607357</s>
ANSWER: OMIM:611907

INCORRECT: 39, CORRECT: 43
--------------------------
--------------------------
FALSE
OMIM and brain abnormalities facial dysmorphism Neurodevelopmental disorder with hypotonia is<s> OMIM and brain abnormalities facial dysmorphism Neurodevelopmental disorder with hypotonia is OMIM:617492</s>
ANSWER: OMIM:619383

INCORRECT: 40, CORRECT: 44
--------------------------
FALSE
OMIM ID of 20 familial hypertrophic Cardiomyopathy is<s> OMIM ID of 20 familial hypertrophic Cardiomyopathy is OMIM:608758</s>
ANSWER: OMIM:613876

INCORRECT: 41, CORRECT: 44
--------------------------
FALSE
OMIM 20 familial hypertrophic Cardiomyopathy is<s> OMIM 20 familial hypertrophic Cardiomyopathy is OMIM:608758</s>
ANSWER: OMIM:613876

INCORRECT: 42, CORRECT: 44
--------------------------
-----------

--------------------------
FALSE
OMIM Peeling skin syndrome 3 is<s> OMIM Peeling skin syndrome 3 is OMIM:614232</s>
ANSWER: OMIM:616265

INCORRECT: 72, CORRECT: 98
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
FALSE
OMIM ID of Immunodeficiency 88 is<s> OMIM ID of Immunodeficiency 88 is OMIM:619610</s>
ANSWER: OMIM:619630

INCORRECT: 73, CORRECT: 102
--------------------------
FALSE
OMIM Immunodeficiency 88 is<s> OMIM Immunodeficiency 88 is OMIM:619125</s>
ANSWER: OMIM:619630

INCORRECT: 74, CORRECT: 102
--------------------------
FALSE
OMIM ID of Hereditary motor and sensory neuropathy V is<s> OMIM ID of Hereditary motor and sensory neuropathy V is OMIM:600341</s>
ANSWER: OMIM:600361

INCORRECT: 75, CORRECT: 102
--------------------------
FALSE
OMIM Hereditary motor and sensory neuropathy V is<s> OMIM Hereditary motor and sensory neuropathy V is OMIM:601846</s>
ANSWER: OMIM:600361

INCORRECT: 76, C

--------------------------
FALSE
OMIM Spermatogenic failure 67 is<s> OMIM Spermatogenic failure 67 is OMIM:619703</s>
ANSWER: OMIM:619803

INCORRECT: 108, CORRECT: 144
--------------------------
--------------------------
--------------------------
FALSE
OMIM ID of 2 paroxysmal familial Ventricular fibrillation is<s> OMIM ID of 2 paroxysmal familial Ventricular fibrillation is OMIM:612959</s>
ANSWER: OMIM:612956

INCORRECT: 109, CORRECT: 146
--------------------------
--------------------------
--------------------------
--------------------------
--------------------------
FALSE
OMIM with variant lissencephaly autosomal recessive 34 Intellectual developmental disorder is<s> OMIM with variant lissencephaly autosomal recessive 34 Intellectual developmental disorder is OMIM:614416</s>
ANSWER: OMIM:614499

INCORRECT: 110, CORRECT: 150
--------------------------
--------------------------
FALSE
OMIM Ophthalmoplegic neuromuscular disorder with abnormal mitochondria is<s> OMIM Ophthalmoplegi

...

--------------------------
FALSE
Orphanet Limb-mammary syndrome is<s> Orphanet Limb-mammary syndrome is ORPHA:2367</s>
ANSWER: ORPHA:69085

INCORRECT: 13590, CORRECT: 10332
--------------------------
--------------------------
FALSE
Orphanet Infantile-onset axonal motor and sensory neuropathy-optic atrophy-neurodegenerative syndrome is<s> Orphanet Infantile-onset axonal motor and sensory neuropathy-optic atrophy-neurodegenerative syndrome is ORPHA:459332</s>
ANSWER: ORPHA:457205

INCORRECT: 13591, CORRECT: 10333
--------------------------
FALSE
Orphanet ID of Rosaï-Dorfman disease is<s> Orphanet ID of Rosaï-Dorfman disease is ORPHA:293488</s>
ANSWER: ORPHA:158014

INCORRECT: 13592, CORRECT: 10333
--------------------------
FALSE
Orphanet Rosaï-Dorfman disease is<s> Orphanet Rosaï-Dorfman disease is ORPHA:397951</s>
ANSWER: ORPHA:158014

INCORRECT: 13593, CORRECT: 10333
--------------------------
FALSE
Orphanet ID of Hypertrichosis lanuginosa congenita is<s> Orphanet ID of Hypertrichosi

--------------------------
FALSE
Orphanet ID of Pyruvate dehydrogenase E3-binding protein deficiency is<s> Orphanet ID of Pyruvate dehydrogenase E3-binding protein deficiency is ORPHA:255888</s>
ANSWER: ORPHA:255182

INCORRECT: 13628, CORRECT: 10339
--------------------------
FALSE
Orphanet Pyruvate dehydrogenase E3-binding protein deficiency is<s> Orphanet Pyruvate dehydrogenase E3-binding protein deficiency is ORPHA:251113</s>
ANSWER: ORPHA:255182

INCORRECT: 13629, CORRECT: 10339
--------------------------
FALSE
Orphanet ID of Maternal hyperthermia-induced birth defects is<s> Orphanet ID of Maternal hyperthermia-induced birth defects is ORPHA:2280</s>
ANSWER: ORPHA:2216

INCORRECT: 13630, CORRECT: 10339
--------------------------
FALSE
Orphanet Maternal hyperthermia-induced birth defects is<s> Orphanet Maternal hyperthermia-induced birth defects is ORPHA:2280</s>
ANSWER: ORPHA:2216

INCORRECT: 13631, CORRECT: 10339
--------------------------
FALSE
Orphanet ID of Kozlowski-Tsuruta ty

--------------------------
FALSE
Orphanet Multifocal lymphangioendotheliomatosis-thrombocytopenia syndrome is<s> Orphanet Multifocal lymphangioendotheliomatosis-thrombocytopenia syndrome is ORPHA:52811</s>
ANSWER: ORPHA:464321

INCORRECT: 13664, CORRECT: 10356
--------------------------
--------------------------
FALSE
Orphanet Hypoxanthine guanine phosphoribosyltransferase partial deficiency is<s> Orphanet Hypoxanthine guanine phosphoribosyltransferase partial deficiency is ORPHA:263801</s>
ANSWER: ORPHA:79233

INCORRECT: 13665, CORRECT: 10357
--------------------------
FALSE
Orphanet ID of Crigler-Najjar syndrome type 1 is<s> Orphanet ID of Crigler-Najjar syndrome type 1 is ORPHA:79100</s>
ANSWER: ORPHA:79234

INCORRECT: 13666, CORRECT: 10357
--------------------------
FALSE
Orphanet Crigler-Najjar syndrome type 1 is<s> Orphanet Crigler-Najjar syndrome type 1 is ORPHA:2058</s>
ANSWER: ORPHA:79234

INCORRECT: 13667, CORRECT: 10357
--------------------------
FALSE
Orphanet ID of Crigle

--------------------------
--------------------------
FALSE
Orphanet Neonatal alloimmune neutropenia is<s> Orphanet Neonatal alloimmune neutropenia is ORPHA:284362</s>
ANSWER: ORPHA:464370

INCORRECT: 13703, CORRECT: 10371
--------------------------
FALSE
Orphanet ID of B3GALT6-related spondylodysplastic Ehlers-Danlos syndrome is<s> Orphanet ID of B3GALT6-related spondylodysplastic Ehlers-Danlos syndrome is ORPHA:536466</s>
ANSWER: ORPHA:536467

INCORRECT: 13704, CORRECT: 10371
--------------------------
FALSE
Orphanet B3GALT6-related spondylodysplastic Ehlers-Danlos syndrome is<s> Orphanet B3GALT6-related spondylodysplastic Ehlers-Danlos syndrome is ORPHA:509466</s>
ANSWER: ORPHA:536467

INCORRECT: 13705, CORRECT: 10371
--------------------------
FALSE
Orphanet ID of classic type Autosomal recessive cutis laxa type 2 is<s> Orphanet ID of classic type Autosomal recessive cutis laxa type 2 is ORPHA:357077</s>
ANSWER: ORPHA:357074

INCORRECT: 13706, CORRECT: 10371
-----------------------

--------------------------
FALSE
Orphanet ID of Pseudomyxoma peritonei is<s> Orphanet ID of Pseudomyxoma peritonei is ORPHA:27108</s>
ANSWER: ORPHA:26790

INCORRECT: 13738, CORRECT: 10377
--------------------------
FALSE
Orphanet Pseudomyxoma peritonei is<s> Orphanet Pseudomyxoma peritonei is ORPHA:2970</s>
ANSWER: ORPHA:26790

INCORRECT: 13739, CORRECT: 10377
--------------------------
FALSE
Orphanet ID of Multiple acyl-CoA dehydrogenase deficiency is<s> Orphanet ID of Multiple acyl-CoA dehydrogenase deficiency is ORPHA:26781</s>
ANSWER: ORPHA:26791

INCORRECT: 13740, CORRECT: 10377
--------------------------
FALSE
Orphanet Multiple acyl-CoA dehydrogenase deficiency is<s> Orphanet Multiple acyl-CoA dehydrogenase deficiency is ORPHA:26781</s>
ANSWER: ORPHA:26791

INCORRECT: 13741, CORRECT: 10377
--------------------------
FALSE
Orphanet ID of Short chain acyl-CoA dehydrogenase deficiency is<s> Orphanet ID of Short chain acyl-CoA dehydrogenase deficiency is ORPHA:26790</s>
ANSWER: ORPHA

In [ ]:
print(f"finished validating on untrained sentences")
print(f"total correct: {totalCorrect}")
print(f"total incorrect: {totalIncorrect}")